# Import libraries

In [2]:
# Importing required modules
import pandas as pd
from openai import OpenAI
from tenacity import retry, stop_after_attempt, wait_random_exponential
import io
import os
import json
import asyncio
from openai import AsyncOpenAI
import time

In [3]:
from dotenv import load_dotenv
# Load the .env file
load_dotenv()

True

In [4]:
import logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s',
                        handlers=[
        logging.FileHandler("../data/find_promises_log_20240101.log"),  # Log messages are written to this file
        logging.StreamHandler()  # Log messages are also printed to the console
    ]
)

In [5]:
import nest_asyncio
nest_asyncio.apply()

# Prepare the database

In [27]:
promises = pd.read_csv("../data/sxp1500_presentations_ceo_aggregated_promises_expanded_cleaned_transcriptlevel_horizon.csv")

/var/folders/qr/1pq07r555gxgt22gqksl2tlw0000gn/T/ipykernel_78414/947927481.py:1: DtypeWarning: Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.
  promises = pd.read_csv("../data/LIWC-22 Results - sxp1500_presentations_ceo_aggr___ - LIWC Analysis_v11_horizon_v2.csv")


In [28]:
list(promises.columns)

['Unnamed: 0',
 'transcriptid',
 'transcriptcomponentid_list',
 'audiolengthsec',
 'companyid',
 'companyname',
 'companyofperson',
 'componentorder',
 'componenttextpreview',
 'delayreasontypeid',
 'delayreasontypename',
 'exec_fullname',
 'execid',
 'gvkey',
 'headline',
 'is_ceo',
 'isdelayed_flag',
 'keydeveventtypeid',
 'keydeveventtypename',
 'keydevid',
 'matched_name',
 'mostimportantdateutc',
 'mostimportanttimeutc',
 'proid',
 'speakertypeid',
 'speakertypename',
 'transcriptcollectiontypeid',
 'transcriptcollectiontypename',
 'transcriptcomponenttypeid',
 'transcriptcomponenttypename',
 'transcriptcreationdate_utc',
 'transcriptcreationtime_utc',
 'transcriptpersonid',
 'transcriptpersonname',
 'transcriptpresentationtypeid',
 'transcriptpresentationtypename',
 'word_count',
 'year',
 'transcript_text_len',
 'transcriptcomponentid_ceospeech',
 'processed',
 '3-promise-horizon-v2',
 '1-promise-verbatim',
 '2-promise-explain',
 '3-promise-delivery-time',
 '4-promise-horizon',


In [29]:
promises['processed'] = 0
promises['result'] = None

## Setting the parameters

In [9]:
# Adjust these values based on your needs
CONCURRENT_REQUESTS = 2500  # Maximum number of concurrent requests
TIMEOUT = 240  # Timeout in seconds for each request

# Constants
batch_size = 5000  # Number of requests after which to checkpoint
save_file = '../data/sxp1500_presentations_ceo_aggregated_promises_expanded_cleaned_transcriptlevel_horizon_specificity.pkl'

# for sample run
#initial_file = '../data/sample_transcripts.pkl'

open_ai_api_key="..."

## Batch promise identification functions

In [10]:
user_message_template = """
*** Role: You are an expert financial analyst specializing in evaluating corporate communications. Your task is to assess how specific the CEO promises are, based solely on their clarity and measurability. Ignore considerations of feasibility, strategic importance, or tone—focus only on what is clearly defined and measurable.
*** Task: Evaluate the specificity of the following CEO promise, extracted from an earnings call transcript. Assign a specificity score on a scale of 1 to 5 (with 5 being the most specific) and justify your rating by highlighting measurable elements such as specific metrics, defined timeframes, or clear deliverables.

*** Specificity Rating Scale:
	•	1 - Very Vague:General statement of intent or aspiration without concrete details, metrics, timelines, or defined scope.Examples: "We will focus on growth," "We aim to improve efficiency," "We are committed to innovation."
	•	2 - Somewhat Vague:Mentions a specific area or goal but lacks quantifiable metrics, clear timelines, or specific actions. May include ambiguous qualifiers.Examples: "We expect to see significant improvement in margins," "We plan to launch new products next year," "We will strengthen our market position."
	•	3 - Moderately Specific:Provides some concrete details such as a target area or a general timeframe or a qualitative metric, but key elements (like specific numbers or deliverable details) are missing or unclear.Examples: "We will reduce operating costs in the second half," "We aim for double-digit revenue growth," "We will expand into the European market."
	•	4 - Specific:Clearly defines the goal with either a quantifiable metric or target. The action or outcome is well-defined.Examples: "We will launch Product X by Q4," "We are targeting a 5% increase in market share," "We will achieve positive cash flow next fiscal year."
	•	5 - Very Specific:Clearly defines the goal, includes specific, quantifiable metrics or targets, and provides a clear timeframe or deadline. The promise's scope and nature are unambiguous.Examples: "We will reduce SG&A expenses by $10 million in fiscal year 2026," "We will launch the Alpha platform in North America by June 30th," "We will increase recurring revenue to 60% of total revenue within 18 months."

*** Input Promise:
{{input_promise}}

*** Output Format:
Please provide your response in the following JSON format:
{ "thinking": "[Provide a brief explanation for your score, referencing elements such as the presence or absence of measurable metrics, clear timelines, and deliverable details based on the scale definitions]",
  "specificity_score": [Assign a score from 1 to 5 based on the scale above]
}

"""


# CORRECTED:
def create_user_message(row, user_message_template):
    # Ensure data is string type for replacement, handle potential NaNs
    promise_verbatim = str(row["1-promise-verbatim"]) if pd.notna(row["1-promise-verbatim"]) else ""

    user_message = user_message_template.replace("{{input_promise}}", promise_verbatim)
    return user_message

In [11]:

client = AsyncOpenAI(api_key=open_ai_api_key)

# Semaphore to control the number of concurrent requests
semaphore = asyncio.Semaphore(CONCURRENT_REQUESTS)


In [12]:

@retry(stop=stop_after_attempt(3), wait=wait_random_exponential(multiplier=1, max=10))
async def fetch_chat_completion(user_message, index):
    async with semaphore:
        logging.info(f"Processing request for row {index}")
        try:
            response = await asyncio.wait_for(client.chat.completions.create(
                model="gpt-4o",
                seed=2025,
                temperature=0.0,
                response_format={"type": "json_object"},
                messages=[{"role": "user", "content": user_message}]
            ), TIMEOUT)
            logging.info(f"Completed request for row {index}")
            return response
        except Exception as e:
            logging.error(f"Error in request for row {index}: {e}")
            return None

async def process_rows(df, BATCH_SIZE, save_file):
    df_non_processed = df[df['processed'] == 0]

    total_prompt_tokens = 0
    total_completion_tokens = 0

    for start_index in range(0, len(df_non_processed), BATCH_SIZE):
        end_index = start_index + BATCH_SIZE
        batch_df = df_non_processed.iloc[start_index:end_index]
        
        task_list = [
            (index, asyncio.create_task(fetch_chat_completion(create_user_message(row, user_message_template), index)))
            for index, row in batch_df.iterrows()
        ]
        responses = await asyncio.gather(*[task for index, task in task_list], return_exceptions=True)
        
        for (index, _), response in zip(task_list, responses):
            if isinstance(response, Exception):
                df.at[index, 'result'] = None
            elif response is None or pd.isna(response.choices[0].message.content) or response.choices[0].message.content == '' or response.choices[0].message.content == 'None':
                df.at[index, 'result'] = None

                try:
                    total_prompt_tokens += response.usage.prompt_tokens
                except:
                    pass
            else:
                df.at[index, 'result'] = response.choices[0].message.content
                df.at[index, 'processed'] = 1

                try:
                    total_prompt_tokens += response.usage.prompt_tokens
                    total_completion_tokens += response.usage.completion_tokens
                except:
                    pass

        # Save intermediate results
        df.to_pickle(save_file)
        

    # Account for responses that are None, NaN, or empty
    df['result'] = df['result'].replace('', None).replace(float('nan'), None)
    df.to_pickle(save_file)
    return df, total_prompt_tokens, total_completion_tokens


# Running the asynchronous tasks with checkpointing
async def main(batch_size, save_file):
    # check if save file exists
    
    # Process remaining rows
    results_df, total_prompt_tokens, total_completion_tokens = await process_rows(promises, batch_size, save_file)
    return results_df, total_prompt_tokens, total_completion_tokens



In [ ]:
# Execute the main function in Jupyter notebook
results, total_prompt_tokens, total_completion_tokens = await main(batch_size, save_file)

2025-04-08 10:30:16,436 - INFO - Processing request for row 0
2025-04-08 10:30:16,438 - INFO - Processing request for row 1
2025-04-08 10:30:16,439 - INFO - Processing request for row 2
2025-04-08 10:30:16,439 - INFO - Processing request for row 3
2025-04-08 10:30:16,440 - INFO - Processing request for row 4
2025-04-08 10:30:16,440 - INFO - Processing request for row 5
2025-04-08 10:30:16,441 - INFO - Processing request for row 6
2025-04-08 10:30:16,441 - INFO - Processing request for row 7
2025-04-08 10:30:16,441 - INFO - Processing request for row 8
2025-04-08 10:30:16,442 - INFO - Processing request for row 9
2025-04-08 10:30:16,442 - INFO - Processing request for row 10
2025-04-08 10:30:16,443 - INFO - Processing request for row 11
2025-04-08 10:30:16,443 - INFO - Processing request for row 12
2025-04-08 10:30:16,444 - INFO - Processing request for row 13
2025-04-08 10:30:16,444 - INFO - Processing request for row 14
2025-04-08 10:30:16,445 - INFO - Processing request for row 15
20

# Continue if disrupted

In [7]:
promises_continue = pd.read_pickle("../data/sxp1500_presentations_ceo_aggregated_promises_expanded_cleaned_transcriptlevel_horizon_specificity.pkl")

# Running the asynchronous tasks with checkpointing
async def main_continue(batch_size, save_file):
    # check if save file exists
    
    # Process remaining rows
    results_df, total_prompt_tokens, total_completion_tokens = await process_rows(promises_continue, batch_size, save_file)
    return results_df, total_prompt_tokens, total_completion_tokens


In [13]:
# Execute the main function in Jupyter notebook
results, total_prompt_tokens, total_completion_tokens = await main_continue(batch_size, save_file)

2025-04-08 13:03:04,741 - INFO - Processing request for row 14191
2025-04-08 13:03:04,742 - INFO - Processing request for row 14192
2025-04-08 13:03:04,742 - INFO - Processing request for row 14196
2025-04-08 13:03:04,743 - INFO - Processing request for row 14203
2025-04-08 13:03:04,743 - INFO - Processing request for row 14206
2025-04-08 13:03:04,744 - INFO - Processing request for row 14212
2025-04-08 13:03:04,744 - INFO - Processing request for row 14215
2025-04-08 13:03:04,745 - INFO - Processing request for row 14217
2025-04-08 13:03:04,745 - INFO - Processing request for row 14220
2025-04-08 13:03:04,746 - INFO - Processing request for row 14224
2025-04-08 13:03:04,747 - INFO - Processing request for row 14245
2025-04-08 13:03:04,747 - INFO - Processing request for row 14249
2025-04-08 13:03:04,748 - INFO - Processing request for row 14255
2025-04-08 13:03:04,748 - INFO - Processing request for row 14264
2025-04-08 13:03:04,749 - INFO - Processing request for row 14403
2025-04-08

In [14]:
list(results['result'])



['{\n  "thinking": "The CEO promise mentions the submission of a paper for peer review and the preparation of a second paper, with an expectation of publication over the next few months. However, it lacks specific, quantifiable metrics or a precise timeline for when the publications will occur. The timeframe \'over the next few months\' is somewhat vague, and there are no specific deliverables or metrics provided. The promise to announce future publications is also non-specific regarding timing or content.",\n  "specificity_score": 2\n}',
 '{\n  "thinking": "The CEO promise includes a specific goal of registering 2,100 patients, which is a quantifiable metric. However, the timeframe is vague, as it mentions \'over the next several years\' without a clear deadline. The promise also includes the intention to publish results, but it lacks specific details on when this will occur. While the promise is clear about the number of patients, the lack of a precise timeframe for both patient enro

# Cleaning up the specificity columns

In [22]:
promises = pd.read_pickle("../data/sxp1500_presentations_ceo_aggregated_promises_expanded_cleaned_transcriptlevel_horizon_specificity.pkl")

In [18]:
# Extract the specificity_score from the result column
import json

# Display a sample result
print(promises.iloc[1]['result'])

# Create a new column for specificity_score
promises['specificity_score'] = promises['result'].apply(
    lambda x: json.loads(x).get('specificity_score') if isinstance(x, str) and x.strip() else None
)

# Show the first few rows with the new column
promises[['result', 'specificity_score']].head()

{
  "thinking": "The CEO promise includes a specific goal of registering 2,100 patients, which is a quantifiable metric. However, the timeframe is vague, as it mentions 'over the next several years' without a clear deadline. The promise also includes the intention to publish results, but it lacks specific details on when this will occur. While the promise is clear about the number of patients, the lack of a precise timeframe for both patient enrollment completion and publication of results reduces its specificity.",
  "specificity_score": 3
}


result  specificity_score
0  {\n  "thinking": "The CEO promise mentions the...                2.0
1  {\n  "thinking": "The CEO promise includes a s...                3.0
2  {\n  "thinking": "The promise specifies a clea...                4.0
3  {\n  "thinking": "The CEO's promise mentions a...                3.0
4  {\n  "thinking": "The CEO promise is very spec...                5.0

In [19]:
promises[ 'specificity_score'].describe()

count    165992.000000
mean          2.891823
std           1.457577
min           1.000000
25%           1.000000
50%           3.000000
75%           4.000000
max           5.000000
Name: specificity_score, dtype: float64

In [20]:
# rename column results to 3-promise-horizon-v2
promises.to_csv("../data/sxp1500_presentations_ceo_aggregated_promises_expanded_cleaned_transcriptlevel_horizon_specificity.csv", index=False)